# Analysis of FEIc1-FEIc16 contracts
---
Plotting Price vs Time, Volume vs Time and Heatmaps

## FEIc1

### Price vs Time and Volume vs Time

In [70]:
import plotly.graph_objs as go
import pandas as pd
import os

def plot_price_and_volume_dual_axis(file_path):
    """
    Plot interactive price (Close) and volume vs time on the same graph using Plotly with dual y-axes.
    Only days with trading activity are shown on the x-axis.
    """
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    title = os.path.basename(file_path)

    # Filter to only days with trading (i.e., at least one nonzero volume)
    df = df[df['Volume'] > 0]
    trading_days = df['Date-Time'].dt.normalize().unique()
    df = df[df['Date-Time'].dt.normalize().isin(trading_days)]

    fig = go.Figure()

    # Price (Close) line on primary y-axis
    fig.add_trace(go.Scatter(
        x=df['Date-Time'],
        y=df['Close'],
        name='Close Price',
        mode='lines',
        line=dict(color='blue'),
        yaxis='y1'
    ))

    # Volume bar on secondary y-axis
    fig.add_trace(go.Bar(
        x=df['Date-Time'],
        y=df['Volume'],
        name='Volume',
        marker_color='orange',
        opacity=0.4,
        yaxis='y2'
    ))

    fig.update_layout(
        title=f'Close Price and Volume vs Time - {title}',
        xaxis=dict(
            title='Date-Time',
            type='category',  # Only show days with trading
            tickmode='array',
            tickvals=[d for d in df['Date-Time'][::max(1, len(df)//10)]],  # Show a subset of ticks for readability
            tickformat='%Y-%m-%d'
        ),
        yaxis=dict(title='Close Price', side='left'),
        yaxis2=dict(title='Volume', overlaying='y', side='right', showgrid=False),
        legend=dict(orientation='h'),
        height=700,
        bargap=0,
        xaxis_rangeslider_visible=True,
        hovermode='x unified'
    )

    fig.show()

# Example usage:
# plot_price_and_volume_dual_axis('C:/Users/ishan.ostwal/OneDrive - hertshtengroup.com/Documents/FF_DataAnalysis/Assignment1/Cleaned_Data/resampled_1d/FEIc1_ohlcv_1d.csv')
plot_price_and_volume_dual_axis('Cleaned_Data/resampled_1d/FEIc1_ohlcv_1d.csv')

### Returns Distribution

In [99]:
def plot_standardized_return_histogram(file_path, tick_value=.005):
    """
    Plot a histogram of returns (in ticks) for the contract, with the x-axis as returns (not z-score),
    show SD lines at -3, -2, -1, 0, 1, 2, 3 (in return units), and center the plot with more bins.
    """
    import plotly.graph_objs as go
    import pandas as pd
    df = pd.read_csv(file_path)
    title = os.path.basename(file_path)
    # Calculate tick changes
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_value
    df = df.dropna(subset=['Return'])
    mean = df['Return'].mean()
    std = df['Return'].std()
    # Center the histogram around mean, set more bins
    min_ret = df['Return'].min()
    max_ret = df['Return'].max()
    range_padding = max(abs(min_ret - mean), abs(max_ret - mean))
    x_range = [mean - range_padding, mean + range_padding]
    fig = go.Figure()
    fig.add_trace(go.Histogram(
        x=df['Return'],
        nbinsx=300,  # More bins for finer bars
        name='Return (in ticks)',
        marker_color='green',
        opacity=0.7,
        xbins=dict(
            start=x_range[0],
            end=x_range[1],
            size=(x_range[1] - x_range[0]) / 300
        )
    ))
    # Add vertical lines and return annotations for SDs (in return units)
    for sd in [-3, -2, -1, 0, 1, 2, 3]:
        ret = mean + sd * std
        fig.add_shape(
            type='line',
            x0=ret, x1=ret,
            y0=0, y1=1,
            yref='paper',
            line=dict(
                color='red' if sd == 0 else 'gray',
                width=2 if sd == 0 else 1,
                dash='dash' if sd != 0 else 'solid'
            )
        )
        fig.add_annotation(
            x=ret,
            y=1,
            yref='paper',
            text=f'SD={sd}<br>Return={ret:.4f}',
            showarrow=False,
            yshift=10 if sd > 0 else -10,
            font=dict(color='red' if sd == 0 else 'gray')
        )
    fig.update_layout(
        title=f'Return Distribution (in ticks) - {title}',
        xaxis_title='Return (in ticks)',
        yaxis_title='Frequency',
        height=500,
        bargap=0.01,
        xaxis=dict(range=x_range, zeroline=True, zerolinewidth=2, zerolinecolor='black')
    )
    fig.show()

# Example usage:
# plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc1_ohlcv_1d.csv')
plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc1_ohlcv_1d.csv')

### Moving Averages and Bollinger Bands

In [72]:
def plot_ma_bollinger_bands(file_path):
    """
    Plot Close price with 10, 50, 100 period moving averages and their respective Bollinger Bands (±2 std).
    The color of each MA and its Bollinger Band is the same (with bands as transparent fill).
    Also plot rolling volatility (std) for each MA window on a secondary y-axis (right side).
    """
    import pandas as pd
    import plotly.graph_objs as go
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    
    ma_periods = [10, 50, 100]
    ma_colors = ['blue', 'orange', 'green']
    
    fig = go.Figure()
    # Plot Close price (darker color)
    fig.add_trace(go.Scatter(
        x=df['Date-Time'], y=df['Close'], name='Close',
        line=dict(color='black', width=2.5), opacity=1, yaxis='y1'
    ))
    
    for period, color in zip(ma_periods, ma_colors):
        ma = df['Close'].rolling(window=period).mean()
        std = df['Close'].rolling(window=period).std()
        # Extrapolate MA and std to initial dates by linear extrapolation (using first two valid values)
        first_valid = ma.first_valid_index()
        if first_valid is not None and first_valid > 0:
            # Linear extrapolation for MA
            next_valid = ma[first_valid+1:first_valid+2].index
            if len(next_valid) > 0:
                slope_ma = (ma[next_valid[0]] - ma[first_valid]) / (next_valid[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    ma[i] = ma[i+1] - slope_ma
            # Linear extrapolation for std
            next_valid_std = std[first_valid+1:first_valid+2].index
            if len(next_valid_std) > 0:
                slope_std = (std[next_valid_std[0]] - std[first_valid]) / (next_valid_std[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    std[i] = std[i+1] - slope_std
        upper = ma + 2 * std
        lower = ma - 2 * std
        # MA line
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=ma, name=f'MA{period}',
            line=dict(color=color, width=2), yaxis='y1'
        ))
        # Bollinger Band (upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=upper, name=f'BB{period} Upper',
            line=dict(color=color, width=1, dash='dot'),
            showlegend=False, yaxis='y1'
        ))
        # Bollinger Band (lower, fill to upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=lower, name=f'BB{period} Lower',
            line=dict(color=color, width=1, dash='dot'),
            fill='tonexty', fillcolor='rgba(0,0,0,0.07)',
            opacity=0.2, showlegend=False, yaxis='y1'
        ))
        # Volatility (right y-axis)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=std, name=f'Volatility {period}',
            line=dict(color=color, width=2, dash='dash'),
            opacity=0.8, yaxis='y2'
        ))
    
    fig.update_layout(
        title='Close Price with Moving Averages, Bollinger Bands, and Volatility',
        xaxis_title='Date-Time',
        yaxis=dict(title='Price', side='left'),
        yaxis2=dict(title='Volatility', overlaying='y', side='right', showgrid=False),
        height=800,
        legend=dict(orientation='h', yanchor='bottom', y=1.02, xanchor='right', x=1)
    )
    fig.show()

# Example usage:
# plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc1_ohlcv_1d.csv')
plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc1_ohlcv_1d.csv')

### Weekly and Monthly Heatmaps of Volume Traded and Returns

The following cell generates heatmaps showing the sum of volume traded and the sum of returns, grouped by ISO week (using the actual Monday-Sunday date range for each week) and by month, for quick visual analysis of trading activity and return patterns. Non-trading days are skipped in the aggregation.

In [100]:
import pandas as pd
import plotly.express as px
from datetime import timedelta

def plot_volume_return_heatmaps(file_path, tick_size=0.005):
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    df['Date'] = df['Date-Time'].dt.date
    df['Year'] = df['Date-Time'].dt.isocalendar().year
    df['ISO_Week'] = df['Date-Time'].dt.isocalendar().week
    df['Month'] = df['Date-Time'].dt.month

    # Calculate returns as tick changes with configurable tick_size parameter
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_size
    df = df.dropna(subset=['Return'])

    # Group by ISO week (Monday-Sunday)
    df['WeekStart'] = df['Date-Time'].dt.to_period('W-MON').apply(lambda r: r.start_time.date())
    df['WeekEnd'] = df['WeekStart'] + timedelta(days=6)
    weekly = df.groupby(['Year', 'ISO_Week', 'WeekStart', 'WeekEnd']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    weekly['DateRange'] = weekly.apply(lambda x: f"{x['WeekStart']} to {x['WeekEnd']}", axis=1)

    # Monthly aggregation (using actual trading months)
    monthly = df.groupby(['Year', 'Month']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    monthly['Year-Month'] = monthly['Year'].astype(str) + '-' + monthly['Month'].astype(str).str.zfill(2)

    # Weekly Volume Heatmap
    fig1 = px.imshow(
        [weekly['Volume'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Volume'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Volume Traded Heatmap (by ISO Week Date Range)'
    )
    fig1.show()

    # Weekly Return Heatmap
    fig2 = px.imshow(
        [weekly['Return'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Return'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Returns Heatmap (by ISO Week Date Range)'
    )
    fig2.show()

    # Monthly Volume Heatmap
    fig3 = px.imshow(
        [monthly['Volume'].values],
        labels=dict(x='Year-Month', y='', color='Volume'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Volume Traded Heatmap'
    )
    fig3.show()

    # Monthly Return Heatmap
    fig4 = px.imshow(
        [monthly['Return'].values],
        labels=dict(x='Year-Month', y='', color='Return'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Returns Heatmap'
    )
    fig4.show()

# Example usage:
# plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc1_ohlcv_1d.csv')
plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc1_ohlcv_1d.csv')

c:\ProgramData\anaconda3\lib\site-packages\pandas\core\arrays\datetimes.py:1162: UserWarning:

Converting to PeriodArray/Index representation will drop timezone information.



## FEIc2

### Price vs Time and Volume vs Time

In [74]:
import plotly.graph_objs as go
import pandas as pd
import os

def plot_price_and_volume_dual_axis(file_path):
    """
    Plot interactive price (Close) and volume vs time on the same graph using Plotly with dual y-axes.
    Only days with trading activity are shown on the x-axis.
    """
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    title = os.path.basename(file_path)

    # Filter to only days with trading (i.e., at least one nonzero volume)
    df = df[df['Volume'] > 0]
    trading_days = df['Date-Time'].dt.normalize().unique()
    df = df[df['Date-Time'].dt.normalize().isin(trading_days)]

    fig = go.Figure()

    # Price (Close) line on primary y-axis
    fig.add_trace(go.Scatter(
        x=df['Date-Time'],
        y=df['Close'],
        name='Close Price',
        mode='lines',
        line=dict(color='blue'),
        yaxis='y1'
    ))

    # Volume bar on secondary y-axis
    fig.add_trace(go.Bar(
        x=df['Date-Time'],
        y=df['Volume'],
        name='Volume',
        marker_color='orange',
        opacity=0.4,
        yaxis='y2'
    ))

    fig.update_layout(
        title=f'Close Price and Volume vs Time - {title}',
        xaxis=dict(
            title='Date-Time',
            type='category',  # Only show days with trading
            tickmode='array',
            tickvals=[d for d in df['Date-Time'][::max(1, len(df)//10)]],  # Show a subset of ticks for readability
            tickformat='%Y-%m-%d'
        ),
        yaxis=dict(title='Close Price', side='left'),
        yaxis2=dict(title='Volume', overlaying='y', side='right', showgrid=False),
        legend=dict(orientation='h'),
        height=700,
        bargap=0,
        xaxis_rangeslider_visible=True,
        hovermode='x unified'
    )

    fig.show()

# Example usage:
# plot_price_and_volume_dual_axis('C:/Users/ishan.ostwal/OneDrive - hertshtengroup.com/Documents/FF_DataAnalysis/Assignment1/Cleaned_Data/resampled_1d/FEIc2_ohlcv_1d.csv')
plot_price_and_volume_dual_axis('Cleaned_Data/resampled_1d/FEIc2_ohlcv_1d.csv')

### Returns Distribution

In [75]:
def plot_standardized_return_histogram(file_path, tick_value=.005):
    """
    Plot a histogram of returns (in ticks) for the contract, with the x-axis as returns (not z-score),
    show SD lines at -3, -2, -1, 0, 1, 2, 3 (in return units), and center the plot with more bins.
    """
    import plotly.graph_objs as go
    import pandas as pd
    df = pd.read_csv(file_path)
    title = os.path.basename(file_path)
    # Calculate tick changes
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_value
    df = df.dropna(subset=['Return'])
    mean = df['Return'].mean()
    std = df['Return'].std()
    # Center the histogram around mean, set more bins
    min_ret = df['Return'].min()
    max_ret = df['Return'].max()
    range_padding = max(abs(min_ret - mean), abs(max_ret - mean))
    x_range = [mean - range_padding, mean + range_padding]
    fig = go.Figure()
    fig.add_trace(go.Histogram(
        x=df['Return'],
        nbinsx=200,  # More bins for finer bars
        name='Return (in ticks)',
        marker_color='green',
        opacity=0.7,
        xbins=dict(
            start=x_range[0],
            end=x_range[1],
            size=(x_range[1] - x_range[0]) / 200
        )
    ))
    # Add vertical lines and return annotations for SDs (in return units)
    for sd in [-3, -2, -1, 0, 1, 2, 3]:
        ret = mean + sd * std
        fig.add_shape(
            type='line',
            x0=ret, x1=ret,
            y0=0, y1=1,
            yref='paper',
            line=dict(
                color='red' if sd == 0 else 'gray',
                width=2 if sd == 0 else 1,
                dash='dash' if sd != 0 else 'solid'
            )
        )
        fig.add_annotation(
            x=ret,
            y=1,
            yref='paper',
            text=f'SD={sd}<br>Return={ret:.4f}',
            showarrow=False,
            yshift=10 if sd > 0 else -10,
            font=dict(color='red' if sd == 0 else 'gray')
        )
    fig.update_layout(
        title=f'Return Distribution (in ticks) - {title}',
        xaxis_title='Return (in ticks)',
        yaxis_title='Frequency',
        height=500,
        bargap=0.01,
        xaxis=dict(range=x_range, zeroline=True, zerolinewidth=2, zerolinecolor='black')
    )

    fig.show()

# Example usage:
# plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc2_ohlcv_1d.csv')
plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc2_ohlcv_1d.csv')

### Moving Averages and Bollinger Bands

In [76]:
def plot_ma_bollinger_bands(file_path):
    """
    Plot Close price with 10, 50, 100 period moving averages and their respective Bollinger Bands (±2 std).
    The color of each MA and its Bollinger Band is the same (with bands as transparent fill).
    Also plot rolling volatility (std) for each MA window on a secondary y-axis (right side).
    """
    import pandas as pd
    import plotly.graph_objs as go
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    
    ma_periods = [10, 50, 100]
    ma_colors = ['blue', 'orange', 'green']
    
    fig = go.Figure()
    # Plot Close price (darker color)
    fig.add_trace(go.Scatter(
        x=df['Date-Time'], y=df['Close'], name='Close',
        line=dict(color='black', width=2.5), opacity=1, yaxis='y1'
    ))
    
    for period, color in zip(ma_periods, ma_colors):
        ma = df['Close'].rolling(window=period).mean()
        std = df['Close'].rolling(window=period).std()
        # Extrapolate MA and std to initial dates by linear extrapolation (using first two valid values)
        first_valid = ma.first_valid_index()
        if first_valid is not None and first_valid > 0:
            # Linear extrapolation for MA
            next_valid = ma[first_valid+1:first_valid+2].index
            if len(next_valid) > 0:
                slope_ma = (ma[next_valid[0]] - ma[first_valid]) / (next_valid[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    ma[i] = ma[i+1] - slope_ma
            # Linear extrapolation for std
            next_valid_std = std[first_valid+1:first_valid+2].index
            if len(next_valid_std) > 0:
                slope_std = (std[next_valid_std[0]] - std[first_valid]) / (next_valid_std[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    std[i] = std[i+1] - slope_std
        upper = ma + 2 * std
        lower = ma - 2 * std
        # MA line
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=ma, name=f'MA{period}',
            line=dict(color=color, width=2), yaxis='y1'
        ))
        # Bollinger Band (upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=upper, name=f'BB{period} Upper',
            line=dict(color=color, width=1, dash='dot'),
            showlegend=False, yaxis='y1'
        ))
        # Bollinger Band (lower, fill to upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=lower, name=f'BB{period} Lower',
            line=dict(color=color, width=1, dash='dot'),
            fill='tonexty', fillcolor='rgba(0,0,0,0.07)',
            opacity=0.2, showlegend=False, yaxis='y1'
        ))
        # Volatility (right y-axis)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=std, name=f'Volatility {period}',
            line=dict(color=color, width=2, dash='dash'),
            opacity=0.8, yaxis='y2'
        ))
    
    fig.update_layout(
        title='Close Price with Moving Averages, Bollinger Bands, and Volatility',
        xaxis_title='Date-Time',
        yaxis=dict(title='Price', side='left'),
        yaxis2=dict(title='Volatility', overlaying='y', side='right', showgrid=False),
        height=800,
        legend=dict(orientation='h', yanchor='bottom', y=1.02, xanchor='right', x=1)
    )
    fig.show()

# Example usage:
# plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc2_ohlcv_1d.csv')
plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc2_ohlcv_1d.csv')

### Weekly and Monthly Heatmaps of Volume Traded and Returns

The following cell generates heatmaps showing the sum of volume traded and the sum of returns, grouped by ISO week (using the actual Monday-Sunday date range for each week) and by month, for quick visual analysis of trading activity and return patterns. Non-trading days are skipped in the aggregation.

In [77]:
import pandas as pd
import plotly.express as px
from datetime import timedelta

def plot_volume_return_heatmaps(file_path, tick_size=0.005):
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    df['Date'] = df['Date-Time'].dt.date
    df['Year'] = df['Date-Time'].dt.isocalendar().year
    df['ISO_Week'] = df['Date-Time'].dt.isocalendar().week
    df['Month'] = df['Date-Time'].dt.month

    # Calculate returns as tick changes with configurable tick_size parameter
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_size
    df = df.dropna(subset=['Return'])

    # Group by ISO week (Monday-Sunday)
    df['WeekStart'] = df['Date-Time'].dt.to_period('W-MON').apply(lambda r: r.start_time.date())
    df['WeekEnd'] = df['WeekStart'] + timedelta(days=6)
    weekly = df.groupby(['Year', 'ISO_Week', 'WeekStart', 'WeekEnd']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    weekly['DateRange'] = weekly.apply(lambda x: f"{x['WeekStart']} to {x['WeekEnd']}", axis=1)

    # Monthly aggregation (using actual trading months)
    monthly = df.groupby(['Year', 'Month']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    monthly['Year-Month'] = monthly['Year'].astype(str) + '-' + monthly['Month'].astype(str).str.zfill(2)

    # Weekly Volume Heatmap
    fig1 = px.imshow(
        [weekly['Volume'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Volume'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Volume Traded Heatmap (by ISO Week Date Range)'
    )
    fig1.show()

    # Weekly Return Heatmap
    fig2 = px.imshow(
        [weekly['Return'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Return'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Returns Heatmap (by ISO Week Date Range)'
    )
    fig2.show()

    # Monthly Volume Heatmap
    fig3 = px.imshow(
        [monthly['Volume'].values],
        labels=dict(x='Year-Month', y='', color='Volume'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Volume Traded Heatmap'
    )
    fig3.show()

    # Monthly Return Heatmap
    fig4 = px.imshow(
        [monthly['Return'].values],
        labels=dict(x='Year-Month', y='', color='Return'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Returns Heatmap'
    )
    fig4.show()

# Example usage:
# plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc2_ohlcv_1d.csv')
plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc2_ohlcv_1d.csv')

c:\ProgramData\anaconda3\lib\site-packages\pandas\core\arrays\datetimes.py:1162: UserWarning:

Converting to PeriodArray/Index representation will drop timezone information.



## FEIc3

### Price vs Time and Volume vs Time

In [78]:
import plotly.graph_objs as go
import pandas as pd
import os

def plot_price_and_volume_dual_axis(file_path):
    """
    Plot interactive price (Close) and volume vs time on the same graph using Plotly with dual y-axes.
    Only days with trading activity are shown on the x-axis.
    """
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    title = os.path.basename(file_path)

    # Filter to only days with trading (i.e., at least one nonzero volume)
    df = df[df['Volume'] > 0]
    trading_days = df['Date-Time'].dt.normalize().unique()
    df = df[df['Date-Time'].dt.normalize().isin(trading_days)]

    fig = go.Figure()

    # Price (Close) line on primary y-axis
    fig.add_trace(go.Scatter(
        x=df['Date-Time'],
        y=df['Close'],
        name='Close Price',
        mode='lines',
        line=dict(color='blue'),
        yaxis='y1'
    ))

    # Volume bar on secondary y-axis
    fig.add_trace(go.Bar(
        x=df['Date-Time'],
        y=df['Volume'],
        name='Volume',
        marker_color='orange',
        opacity=0.4,
        yaxis='y2'
    ))

    fig.update_layout(
        title=f'Close Price and Volume vs Time - {title}',
        xaxis=dict(
            title='Date-Time',
            type='category',  # Only show days with trading
            tickmode='array',
            tickvals=[d for d in df['Date-Time'][::max(1, len(df)//10)]],  # Show a subset of ticks for readability
            tickformat='%Y-%m-%d'
        ),
        yaxis=dict(title='Close Price', side='left'),
        yaxis2=dict(title='Volume', overlaying='y', side='right', showgrid=False),
        legend=dict(orientation='h'),
        height=700,
        bargap=0,
        xaxis_rangeslider_visible=True,
        hovermode='x unified'
    )

    fig.show()

# Example usage:
# plot_price_and_volume_dual_axis('C:/Users/ishan.ostwal/OneDrive - hertshtengroup.com/Documents/FF_DataAnalysis/Assignment1/Cleaned_Data/resampled_1d/FEIc3_ohlcv_1d.csv')
plot_price_and_volume_dual_axis('Cleaned_Data/resampled_1d/FEIc3_ohlcv_1d.csv')

### Returns Distribution

In [79]:
def plot_standardized_return_histogram(file_path, tick_value=.005):
    """
    Plot a histogram of returns (in ticks) for the contract, with the x-axis as returns (not z-score),
    show SD lines at -3, -2, -1, 0, 1, 2, 3 (in return units), and center the plot with more bins.
    """
    import plotly.graph_objs as go
    import pandas as pd
    df = pd.read_csv(file_path)
    title = os.path.basename(file_path)
    # Calculate tick changes
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_value
    df = df.dropna(subset=['Return'])
    mean = df['Return'].mean()
    std = df['Return'].std()
    # Center the histogram around mean, set more bins
    min_ret = df['Return'].min()
    max_ret = df['Return'].max()
    range_padding = max(abs(min_ret - mean), abs(max_ret - mean))
    x_range = [mean - range_padding, mean + range_padding]
    fig = go.Figure()
    fig.add_trace(go.Histogram(
        x=df['Return'],
        nbinsx=200,  # More bins for finer bars
        name='Return (in ticks)',
        marker_color='green',
        opacity=0.7,
        xbins=dict(
            start=x_range[0],
            end=x_range[1],
            size=(x_range[1] - x_range[0]) / 200
        )
    ))
    # Add vertical lines and return annotations for SDs (in return units)
    for sd in [-3, -2, -1, 0, 1, 2, 3]:
        ret = mean + sd * std
        fig.add_shape(
            type='line',
            x0=ret, x1=ret,
            y0=0, y1=1,
            yref='paper',
            line=dict(
                color='red' if sd == 0 else 'gray',
                width=2 if sd == 0 else 1,
                dash='dash' if sd != 0 else 'solid'
            )
        )
        fig.add_annotation(
            x=ret,
            y=1,
            yref='paper',
            text=f'SD={sd}<br>Return={ret:.4f}',
            showarrow=False,
            yshift=10 if sd > 0 else -10,
            font=dict(color='red' if sd == 0 else 'gray')
        )
    fig.update_layout(
        title=f'Return Distribution (in ticks) - {title}',
        xaxis_title='Return (in ticks)',
        yaxis_title='Frequency',
        height=500,
        bargap=0.01,
        xaxis=dict(range=x_range, zeroline=True, zerolinewidth=2, zerolinecolor='black')
    )

    fig.show()

# Example usage:
# plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc3_ohlcv_1d.csv')
plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc3_ohlcv_1d.csv')

### Moving Averages and Bollinger Bands

In [80]:
def plot_ma_bollinger_bands(file_path):
    """
    Plot Close price with 10, 50, 100 period moving averages and their respective Bollinger Bands (±2 std).
    The color of each MA and its Bollinger Band is the same (with bands as transparent fill).
    Also plot rolling volatility (std) for each MA window on a secondary y-axis (right side).
    """
    import pandas as pd
    import plotly.graph_objs as go
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    
    ma_periods = [10, 50, 100]
    ma_colors = ['blue', 'orange', 'green']
    
    fig = go.Figure()
    # Plot Close price (darker color)
    fig.add_trace(go.Scatter(
        x=df['Date-Time'], y=df['Close'], name='Close',
        line=dict(color='black', width=2.5), opacity=1, yaxis='y1'
    ))
    
    for period, color in zip(ma_periods, ma_colors):
        ma = df['Close'].rolling(window=period).mean()
        std = df['Close'].rolling(window=period).std()
        # Extrapolate MA and std to initial dates by linear extrapolation (using first two valid values)
        first_valid = ma.first_valid_index()
        if first_valid is not None and first_valid > 0:
            # Linear extrapolation for MA
            next_valid = ma[first_valid+1:first_valid+2].index
            if len(next_valid) > 0:
                slope_ma = (ma[next_valid[0]] - ma[first_valid]) / (next_valid[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    ma[i] = ma[i+1] - slope_ma
            # Linear extrapolation for std
            next_valid_std = std[first_valid+1:first_valid+2].index
            if len(next_valid_std) > 0:
                slope_std = (std[next_valid_std[0]] - std[first_valid]) / (next_valid_std[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    std[i] = std[i+1] - slope_std
        upper = ma + 2 * std
        lower = ma - 2 * std
        # MA line
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=ma, name=f'MA{period}',
            line=dict(color=color, width=2), yaxis='y1'
        ))
        # Bollinger Band (upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=upper, name=f'BB{period} Upper',
            line=dict(color=color, width=1, dash='dot'),
            showlegend=False, yaxis='y1'
        ))
        # Bollinger Band (lower, fill to upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=lower, name=f'BB{period} Lower',
            line=dict(color=color, width=1, dash='dot'),
            fill='tonexty', fillcolor='rgba(0,0,0,0.07)',
            opacity=0.2, showlegend=False, yaxis='y1'
        ))
        # Volatility (right y-axis)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=std, name=f'Volatility {period}',
            line=dict(color=color, width=2, dash='dash'),
            opacity=0.8, yaxis='y2'
        ))
    
    fig.update_layout(
        title='Close Price with Moving Averages, Bollinger Bands, and Volatility',
        xaxis_title='Date-Time',
        yaxis=dict(title='Price', side='left'),
        yaxis2=dict(title='Volatility', overlaying='y', side='right', showgrid=False),
        height=800,
        legend=dict(orientation='h', yanchor='bottom', y=1.02, xanchor='right', x=1)
    )
    fig.show()

# Example usage:
# plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc3_ohlcv_1d.csv')
plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc3_ohlcv_1d.csv')

### Weekly and Monthly Heatmaps of Volume Traded and Returns

The following cell generates heatmaps showing the sum of volume traded and the sum of returns, grouped by ISO week (using the actual Monday-Sunday date range for each week) and by month, for quick visual analysis of trading activity and return patterns. Non-trading days are skipped in the aggregation.

In [81]:
import pandas as pd
import plotly.express as px
from datetime import timedelta

def plot_volume_return_heatmaps(file_path, tick_size=0.005):
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    df['Date'] = df['Date-Time'].dt.date
    df['Year'] = df['Date-Time'].dt.isocalendar().year
    df['ISO_Week'] = df['Date-Time'].dt.isocalendar().week
    df['Month'] = df['Date-Time'].dt.month

    # Calculate returns as tick changes with configurable tick_size parameter
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_size
    df = df.dropna(subset=['Return'])

    # Group by ISO week (Monday-Sunday)
    df['WeekStart'] = df['Date-Time'].dt.to_period('W-MON').apply(lambda r: r.start_time.date())
    df['WeekEnd'] = df['WeekStart'] + timedelta(days=6)
    weekly = df.groupby(['Year', 'ISO_Week', 'WeekStart', 'WeekEnd']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    weekly['DateRange'] = weekly.apply(lambda x: f"{x['WeekStart']} to {x['WeekEnd']}", axis=1)

    # Monthly aggregation (using actual trading months)
    monthly = df.groupby(['Year', 'Month']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    monthly['Year-Month'] = monthly['Year'].astype(str) + '-' + monthly['Month'].astype(str).str.zfill(2)

    # Weekly Volume Heatmap
    fig1 = px.imshow(
        [weekly['Volume'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Volume'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Volume Traded Heatmap (by ISO Week Date Range)'
    )
    fig1.show()

    # Weekly Return Heatmap
    fig2 = px.imshow(
        [weekly['Return'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Return'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Returns Heatmap (by ISO Week Date Range)'
    )
    fig2.show()

    # Monthly Volume Heatmap
    fig3 = px.imshow(
        [monthly['Volume'].values],
        labels=dict(x='Year-Month', y='', color='Volume'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Volume Traded Heatmap'
    )
    fig3.show()

    # Monthly Return Heatmap
    fig4 = px.imshow(
        [monthly['Return'].values],
        labels=dict(x='Year-Month', y='', color='Return'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Returns Heatmap'
    )
    fig4.show()

# Example usage:
# plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc3_ohlcv_1d.csv')
plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc3_ohlcv_1d.csv')

c:\ProgramData\anaconda3\lib\site-packages\pandas\core\arrays\datetimes.py:1162: UserWarning:

Converting to PeriodArray/Index representation will drop timezone information.



## FEIc4

### Price vs Time and Volume vs Time

In [82]:
import plotly.graph_objs as go
import pandas as pd
import os

def plot_price_and_volume_dual_axis(file_path):
    """
    Plot interactive price (Close) and volume vs time on the same graph using Plotly with dual y-axes.
    Only days with trading activity are shown on the x-axis.
    """
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    title = os.path.basename(file_path)

    # Filter to only days with trading (i.e., at least one nonzero volume)
    df = df[df['Volume'] > 0]
    trading_days = df['Date-Time'].dt.normalize().unique()
    df = df[df['Date-Time'].dt.normalize().isin(trading_days)]

    fig = go.Figure()

    # Price (Close) line on primary y-axis
    fig.add_trace(go.Scatter(
        x=df['Date-Time'],
        y=df['Close'],
        name='Close Price',
        mode='lines',
        line=dict(color='blue'),
        yaxis='y1'
    ))

    # Volume bar on secondary y-axis
    fig.add_trace(go.Bar(
        x=df['Date-Time'],
        y=df['Volume'],
        name='Volume',
        marker_color='orange',
        opacity=0.4,
        yaxis='y2'
    ))

    fig.update_layout(
        title=f'Close Price and Volume vs Time - {title}',
        xaxis=dict(
            title='Date-Time',
            type='category',  # Only show days with trading
            tickmode='array',
            tickvals=[d for d in df['Date-Time'][::max(1, len(df)//10)]],  # Show a subset of ticks for readability
            tickformat='%Y-%m-%d'
        ),
        yaxis=dict(title='Close Price', side='left'),
        yaxis2=dict(title='Volume', overlaying='y', side='right', showgrid=False),
        legend=dict(orientation='h'),
        height=700,
        bargap=0,
        xaxis_rangeslider_visible=True,
        hovermode='x unified'
    )

    fig.show()

# Example usage:
# plot_price_and_volume_dual_axis('C:/Users/ishan.ostwal/OneDrive - hertshtengroup.com/Documents/FF_DataAnalysis/Assignment1/Cleaned_Data/resampled_1d/FEIc4_ohlcv_1d.csv')
plot_price_and_volume_dual_axis('Cleaned_Data/resampled_1d/FEIc4_ohlcv_1d.csv')

### Returns Distribution

In [83]:
def plot_standardized_return_histogram(file_path, tick_value=.005):
    """
    Plot a histogram of returns (in ticks) for the contract, with the x-axis as returns (not z-score),
    show SD lines at -3, -2, -1, 0, 1, 2, 3 (in return units), and center the plot with more bins.
    """
    import plotly.graph_objs as go
    import pandas as pd
    df = pd.read_csv(file_path)
    title = os.path.basename(file_path)
    # Calculate tick changes
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_value
    df = df.dropna(subset=['Return'])
    mean = df['Return'].mean()
    std = df['Return'].std()
    # Center the histogram around mean, set more bins
    min_ret = df['Return'].min()
    max_ret = df['Return'].max()
    range_padding = max(abs(min_ret - mean), abs(max_ret - mean))
    x_range = [mean - range_padding, mean + range_padding]
    fig = go.Figure()
    fig.add_trace(go.Histogram(
        x=df['Return'],
        nbinsx=200,  # More bins for finer bars
        name='Return (in ticks)',
        marker_color='green',
        opacity=0.7,
        xbins=dict(
            start=x_range[0],
            end=x_range[1],
            size=(x_range[1] - x_range[0]) / 200
        )
    ))
    # Add vertical lines and return annotations for SDs (in return units)
    for sd in [-3, -2, -1, 0, 1, 2, 3]:
        ret = mean + sd * std
        fig.add_shape(
            type='line',
            x0=ret, x1=ret,
            y0=0, y1=1,
            yref='paper',
            line=dict(
                color='red' if sd == 0 else 'gray',
                width=2 if sd == 0 else 1,
                dash='dash' if sd != 0 else 'solid'
            )
        )
        fig.add_annotation(
            x=ret,
            y=1,
            yref='paper',
            text=f'SD={sd}<br>Return={ret:.4f}',
            showarrow=False,
            yshift=10 if sd > 0 else -10,
            font=dict(color='red' if sd == 0 else 'gray')
        )
    fig.update_layout(
        title=f'Return Distribution (in ticks) - {title}',
        xaxis_title='Return (in ticks)',
        yaxis_title='Frequency',
        height=500,
        bargap=0.01,
        xaxis=dict(range=x_range, zeroline=True, zerolinewidth=2, zerolinecolor='black')
    )

    fig.show()

# Example usage:
# plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc4_ohlcv_1d.csv')
plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc4_ohlcv_1d.csv')

### Moving Averages and Bollinger Bands

In [84]:
def plot_ma_bollinger_bands(file_path):
    """
    Plot Close price with 10, 50, 100 period moving averages and their respective Bollinger Bands (±2 std).
    The color of each MA and its Bollinger Band is the same (with bands as transparent fill).
    Also plot rolling volatility (std) for each MA window on a secondary y-axis (right side).
    """
    import pandas as pd
    import plotly.graph_objs as go
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    
    ma_periods = [10, 50, 100]
    ma_colors = ['blue', 'orange', 'green']
    
    fig = go.Figure()
    # Plot Close price (darker color)
    fig.add_trace(go.Scatter(
        x=df['Date-Time'], y=df['Close'], name='Close',
        line=dict(color='black', width=2.5), opacity=1, yaxis='y1'
    ))
    
    for period, color in zip(ma_periods, ma_colors):
        ma = df['Close'].rolling(window=period).mean()
        std = df['Close'].rolling(window=period).std()
        # Extrapolate MA and std to initial dates by linear extrapolation (using first two valid values)
        first_valid = ma.first_valid_index()
        if first_valid is not None and first_valid > 0:
            # Linear extrapolation for MA
            next_valid = ma[first_valid+1:first_valid+2].index
            if len(next_valid) > 0:
                slope_ma = (ma[next_valid[0]] - ma[first_valid]) / (next_valid[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    ma[i] = ma[i+1] - slope_ma
            # Linear extrapolation for std
            next_valid_std = std[first_valid+1:first_valid+2].index
            if len(next_valid_std) > 0:
                slope_std = (std[next_valid_std[0]] - std[first_valid]) / (next_valid_std[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    std[i] = std[i+1] - slope_std
        upper = ma + 2 * std
        lower = ma - 2 * std
        # MA line
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=ma, name=f'MA{period}',
            line=dict(color=color, width=2), yaxis='y1'
        ))
        # Bollinger Band (upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=upper, name=f'BB{period} Upper',
            line=dict(color=color, width=1, dash='dot'),
            showlegend=False, yaxis='y1'
        ))
        # Bollinger Band (lower, fill to upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=lower, name=f'BB{period} Lower',
            line=dict(color=color, width=1, dash='dot'),
            fill='tonexty', fillcolor='rgba(0,0,0,0.07)',
            opacity=0.2, showlegend=False, yaxis='y1'
        ))
        # Volatility (right y-axis)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=std, name=f'Volatility {period}',
            line=dict(color=color, width=2, dash='dash'),
            opacity=0.8, yaxis='y2'
        ))
    
    fig.update_layout(
        title='Close Price with Moving Averages, Bollinger Bands, and Volatility',
        xaxis_title='Date-Time',
        yaxis=dict(title='Price', side='left'),
        yaxis2=dict(title='Volatility', overlaying='y', side='right', showgrid=False),
        height=800,
        legend=dict(orientation='h', yanchor='bottom', y=1.02, xanchor='right', x=1)
    )
    fig.show()

# Example usage:
# plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc4_ohlcv_1d.csv')
plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc4_ohlcv_1d.csv')

### Weekly and Monthly Heatmaps of Volume Traded and Returns

The following cell generates heatmaps showing the sum of volume traded and the sum of returns, grouped by ISO week (using the actual Monday-Sunday date range for each week) and by month, for quick visual analysis of trading activity and return patterns. Non-trading days are skipped in the aggregation.

In [85]:
import pandas as pd
import plotly.express as px
from datetime import timedelta

def plot_volume_return_heatmaps(file_path, tick_size=0.005):
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    df['Date'] = df['Date-Time'].dt.date
    df['Year'] = df['Date-Time'].dt.isocalendar().year
    df['ISO_Week'] = df['Date-Time'].dt.isocalendar().week
    df['Month'] = df['Date-Time'].dt.month

    # Calculate returns as tick changes with configurable tick_size parameter
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_size
    df = df.dropna(subset=['Return'])

    # Group by ISO week (Monday-Sunday)
    df['WeekStart'] = df['Date-Time'].dt.to_period('W-MON').apply(lambda r: r.start_time.date())
    df['WeekEnd'] = df['WeekStart'] + timedelta(days=6)
    weekly = df.groupby(['Year', 'ISO_Week', 'WeekStart', 'WeekEnd']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    weekly['DateRange'] = weekly.apply(lambda x: f"{x['WeekStart']} to {x['WeekEnd']}", axis=1)

    # Monthly aggregation (using actual trading months)
    monthly = df.groupby(['Year', 'Month']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    monthly['Year-Month'] = monthly['Year'].astype(str) + '-' + monthly['Month'].astype(str).str.zfill(2)

    # Weekly Volume Heatmap
    fig1 = px.imshow(
        [weekly['Volume'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Volume'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Volume Traded Heatmap (by ISO Week Date Range)'
    )
    fig1.show()

    # Weekly Return Heatmap
    fig2 = px.imshow(
        [weekly['Return'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Return'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Returns Heatmap (by ISO Week Date Range)'
    )
    fig2.show()

    # Monthly Volume Heatmap
    fig3 = px.imshow(
        [monthly['Volume'].values],
        labels=dict(x='Year-Month', y='', color='Volume'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Volume Traded Heatmap'
    )
    fig3.show()

    # Monthly Return Heatmap
    fig4 = px.imshow(
        [monthly['Return'].values],
        labels=dict(x='Year-Month', y='', color='Return'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Returns Heatmap'
    )
    fig4.show()

# Example usage:
# plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc4_ohlcv_1d.csv')
plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc4_ohlcv_1d.csv')

c:\ProgramData\anaconda3\lib\site-packages\pandas\core\arrays\datetimes.py:1162: UserWarning:

Converting to PeriodArray/Index representation will drop timezone information.



## FEIc5

### Price vs Time and Volume vs Time

In [86]:
import plotly.graph_objs as go
import pandas as pd
import os

def plot_price_and_volume_dual_axis(file_path):
    """
    Plot interactive price (Close) and volume vs time on the same graph using Plotly with dual y-axes.
    Only days with trading activity are shown on the x-axis.
    """
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    title = os.path.basename(file_path)

    # Filter to only days with trading (i.e., at least one nonzero volume)
    df = df[df['Volume'] > 0]
    trading_days = df['Date-Time'].dt.normalize().unique()
    df = df[df['Date-Time'].dt.normalize().isin(trading_days)]

    fig = go.Figure()

    # Price (Close) line on primary y-axis
    fig.add_trace(go.Scatter(
        x=df['Date-Time'],
        y=df['Close'],
        name='Close Price',
        mode='lines',
        line=dict(color='blue'),
        yaxis='y1'
    ))

    # Volume bar on secondary y-axis
    fig.add_trace(go.Bar(
        x=df['Date-Time'],
        y=df['Volume'],
        name='Volume',
        marker_color='orange',
        opacity=0.4,
        yaxis='y2'
    ))

    fig.update_layout(
        title=f'Close Price and Volume vs Time - {title}',
        xaxis=dict(
            title='Date-Time',
            type='category',  # Only show days with trading
            tickmode='array',
            tickvals=[d for d in df['Date-Time'][::max(1, len(df)//10)]],  # Show a subset of ticks for readability
            tickformat='%Y-%m-%d'
        ),
        yaxis=dict(title='Close Price', side='left'),
        yaxis2=dict(title='Volume', overlaying='y', side='right', showgrid=False),
        legend=dict(orientation='h'),
        height=700,
        bargap=0,
        xaxis_rangeslider_visible=True,
        hovermode='x unified'
    )

    fig.show()

# Example usage:
# plot_price_and_volume_dual_axis('C:/Users/ishan.ostwal/OneDrive - hertshtengroup.com/Documents/FF_DataAnalysis/Assignment1/Cleaned_Data/resampled_1d/FEIc5_ohlcv_1d.csv')
plot_price_and_volume_dual_axis('Cleaned_Data/resampled_1d/FEIc5_ohlcv_1d.csv')

### Returns Distribution

In [87]:
def plot_standardized_return_histogram(file_path, tick_value=.005):
    """
    Plot a histogram of returns (in ticks) for the contract, with the x-axis as returns (not z-score),
    show SD lines at -3, -2, -1, 0, 1, 2, 3 (in return units), and center the plot with more bins.
    """
    import plotly.graph_objs as go
    import pandas as pd
    df = pd.read_csv(file_path)
    title = os.path.basename(file_path)
    # Calculate tick changes
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_value
    df = df.dropna(subset=['Return'])
    mean = df['Return'].mean()
    std = df['Return'].std()
    # Center the histogram around mean, set more bins
    min_ret = df['Return'].min()
    max_ret = df['Return'].max()
    range_padding = max(abs(min_ret - mean), abs(max_ret - mean))
    x_range = [mean - range_padding, mean + range_padding]
    fig = go.Figure()
    fig.add_trace(go.Histogram(
        x=df['Return'],
        nbinsx=200,  # More bins for finer bars
        name='Return (in ticks)',
        marker_color='green',
        opacity=0.7,
        xbins=dict(
            start=x_range[0],
            end=x_range[1],
            size=(x_range[1] - x_range[0]) / 200
        )
    ))
    # Add vertical lines and return annotations for SDs (in return units)
    for sd in [-3, -2, -1, 0, 1, 2, 3]:
        ret = mean + sd * std
        fig.add_shape(
            type='line',
            x0=ret, x1=ret,
            y0=0, y1=1,
            yref='paper',
            line=dict(
                color='red' if sd == 0 else 'gray',
                width=2 if sd == 0 else 1,
                dash='dash' if sd != 0 else 'solid'
            )
        )
        fig.add_annotation(
            x=ret,
            y=1,
            yref='paper',
            text=f'SD={sd}<br>Return={ret:.4f}',
            showarrow=False,
            yshift=10 if sd > 0 else -10,
            font=dict(color='red' if sd == 0 else 'gray')
        )
    fig.update_layout(
        title=f'Return Distribution (in ticks) - {title}',
        xaxis_title='Return (in ticks)',
        yaxis_title='Frequency',
        height=500,
        bargap=0.01,
        xaxis=dict(range=x_range, zeroline=True, zerolinewidth=2, zerolinecolor='black')
    )

    fig.show()

# Example usage:
# plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc5_ohlcv_1d.csv')
plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc5_ohlcv_1d.csv')

### Moving Averages and Bollinger Bands

In [88]:
def plot_ma_bollinger_bands(file_path):
    """
    Plot Close price with 10, 50, 100 period moving averages and their respective Bollinger Bands (±2 std).
    The color of each MA and its Bollinger Band is the same (with bands as transparent fill).
    Also plot rolling volatility (std) for each MA window on a secondary y-axis (right side).
    """
    import pandas as pd
    import plotly.graph_objs as go
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    
    ma_periods = [10, 50, 100]
    ma_colors = ['blue', 'orange', 'green']
    
    fig = go.Figure()
    # Plot Close price (darker color)
    fig.add_trace(go.Scatter(
        x=df['Date-Time'], y=df['Close'], name='Close',
        line=dict(color='black', width=2.5), opacity=1, yaxis='y1'
    ))
    
    for period, color in zip(ma_periods, ma_colors):
        ma = df['Close'].rolling(window=period).mean()
        std = df['Close'].rolling(window=period).std()
        # Extrapolate MA and std to initial dates by linear extrapolation (using first two valid values)
        first_valid = ma.first_valid_index()
        if first_valid is not None and first_valid > 0:
            # Linear extrapolation for MA
            next_valid = ma[first_valid+1:first_valid+2].index
            if len(next_valid) > 0:
                slope_ma = (ma[next_valid[0]] - ma[first_valid]) / (next_valid[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    ma[i] = ma[i+1] - slope_ma
            # Linear extrapolation for std
            next_valid_std = std[first_valid+1:first_valid+2].index
            if len(next_valid_std) > 0:
                slope_std = (std[next_valid_std[0]] - std[first_valid]) / (next_valid_std[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    std[i] = std[i+1] - slope_std
        upper = ma + 2 * std
        lower = ma - 2 * std
        # MA line
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=ma, name=f'MA{period}',
            line=dict(color=color, width=2), yaxis='y1'
        ))
        # Bollinger Band (upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=upper, name=f'BB{period} Upper',
            line=dict(color=color, width=1, dash='dot'),
            showlegend=False, yaxis='y1'
        ))
        # Bollinger Band (lower, fill to upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=lower, name=f'BB{period} Lower',
            line=dict(color=color, width=1, dash='dot'),
            fill='tonexty', fillcolor='rgba(0,0,0,0.07)',
            opacity=0.2, showlegend=False, yaxis='y1'
        ))
        # Volatility (right y-axis)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=std, name=f'Volatility {period}',
            line=dict(color=color, width=2, dash='dash'),
            opacity=0.8, yaxis='y2'
        ))
    
    fig.update_layout(
        title='Close Price with Moving Averages, Bollinger Bands, and Volatility',
        xaxis_title='Date-Time',
        yaxis=dict(title='Price', side='left'),
        yaxis2=dict(title='Volatility', overlaying='y', side='right', showgrid=False),
        height=800,
        legend=dict(orientation='h', yanchor='bottom', y=1.02, xanchor='right', x=1)
    )
    fig.show()

# Example usage:
# plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc5_ohlcv_1d.csv')
plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc5_ohlcv_1d.csv')

### Weekly and Monthly Heatmaps of Volume Traded and Returns

The following cell generates heatmaps showing the sum of volume traded and the sum of returns, grouped by ISO week (using the actual Monday-Sunday date range for each week) and by month, for quick visual analysis of trading activity and return patterns. Non-trading days are skipped in the aggregation.

In [89]:
import pandas as pd
import plotly.express as px
from datetime import timedelta

def plot_volume_return_heatmaps(file_path, tick_size=0.005):
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    df['Date'] = df['Date-Time'].dt.date
    df['Year'] = df['Date-Time'].dt.isocalendar().year
    df['ISO_Week'] = df['Date-Time'].dt.isocalendar().week
    df['Month'] = df['Date-Time'].dt.month

    # Calculate returns as tick changes with configurable tick_size parameter
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_size
    df = df.dropna(subset=['Return'])

    # Group by ISO week (Monday-Sunday)
    df['WeekStart'] = df['Date-Time'].dt.to_period('W-MON').apply(lambda r: r.start_time.date())
    df['WeekEnd'] = df['WeekStart'] + timedelta(days=6)
    weekly = df.groupby(['Year', 'ISO_Week', 'WeekStart', 'WeekEnd']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    weekly['DateRange'] = weekly.apply(lambda x: f"{x['WeekStart']} to {x['WeekEnd']}", axis=1)

    # Monthly aggregation (using actual trading months)
    monthly = df.groupby(['Year', 'Month']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    monthly['Year-Month'] = monthly['Year'].astype(str) + '-' + monthly['Month'].astype(str).str.zfill(2)

    # Weekly Volume Heatmap
    fig1 = px.imshow(
        [weekly['Volume'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Volume'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Volume Traded Heatmap (by ISO Week Date Range)'
    )
    fig1.show()

    # Weekly Return Heatmap
    fig2 = px.imshow(
        [weekly['Return'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Return'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Returns Heatmap (by ISO Week Date Range)'
    )
    fig2.show()

    # Monthly Volume Heatmap
    fig3 = px.imshow(
        [monthly['Volume'].values],
        labels=dict(x='Year-Month', y='', color='Volume'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Volume Traded Heatmap'
    )
    fig3.show()

    # Monthly Return Heatmap
    fig4 = px.imshow(
        [monthly['Return'].values],
        labels=dict(x='Year-Month', y='', color='Return'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Returns Heatmap'
    )
    fig4.show()

# Example usage:
# plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc5_ohlcv_1d.csv')
plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc5_ohlcv_1d.csv')

c:\ProgramData\anaconda3\lib\site-packages\pandas\core\arrays\datetimes.py:1162: UserWarning:

Converting to PeriodArray/Index representation will drop timezone information.



## FEIc6

### Price vs Time and Volume vs Time

In [90]:
import plotly.graph_objs as go
import pandas as pd
import os

def plot_price_and_volume_dual_axis(file_path):
    """
    Plot interactive price (Close) and volume vs time on the same graph using Plotly with dual y-axes.
    Only days with trading activity are shown on the x-axis.
    """
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    title = os.path.basename(file_path)

    # Filter to only days with trading (i.e., at least one nonzero volume)
    df = df[df['Volume'] > 0]
    trading_days = df['Date-Time'].dt.normalize().unique()
    df = df[df['Date-Time'].dt.normalize().isin(trading_days)]

    fig = go.Figure()

    # Price (Close) line on primary y-axis
    fig.add_trace(go.Scatter(
        x=df['Date-Time'],
        y=df['Close'],
        name='Close Price',
        mode='lines',
        line=dict(color='blue'),
        yaxis='y1'
    ))

    # Volume bar on secondary y-axis
    fig.add_trace(go.Bar(
        x=df['Date-Time'],
        y=df['Volume'],
        name='Volume',
        marker_color='orange',
        opacity=0.4,
        yaxis='y2'
    ))

    fig.update_layout(
        title=f'Close Price and Volume vs Time - {title}',
        xaxis=dict(
            title='Date-Time',
            type='category',  # Only show days with trading
            tickmode='array',
            tickvals=[d for d in df['Date-Time'][::max(1, len(df)//10)]],  # Show a subset of ticks for readability
            tickformat='%Y-%m-%d'
        ),
        yaxis=dict(title='Close Price', side='left'),
        yaxis2=dict(title='Volume', overlaying='y', side='right', showgrid=False),
        legend=dict(orientation='h'),
        height=700,
        bargap=0,
        xaxis_rangeslider_visible=True,
        hovermode='x unified'
    )

    fig.show()

# Example usage:
# plot_price_and_volume_dual_axis('C:/Users/ishan.ostwal/OneDrive - hertshtengroup.com/Documents/FF_DataAnalysis/Assignment1/Cleaned_Data/resampled_1d/FEIc6_ohlcv_1d.csv')
plot_price_and_volume_dual_axis('Cleaned_Data/resampled_1d/FEIc6_ohlcv_1d.csv')

### Returns Distribution

In [91]:
def plot_standardized_return_histogram(file_path, tick_value=.005):
    """
    Plot a histogram of returns (in ticks) for the contract, with the x-axis as returns (not z-score),
    show SD lines at -3, -2, -1, 0, 1, 2, 3 (in return units), and center the plot with more bins.
    """
    import plotly.graph_objs as go
    import pandas as pd
    df = pd.read_csv(file_path)
    title = os.path.basename(file_path)
    # Calculate tick changes
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_value
    df = df.dropna(subset=['Return'])
    mean = df['Return'].mean()
    std = df['Return'].std()
    # Center the histogram around mean, set more bins
    min_ret = df['Return'].min()
    max_ret = df['Return'].max()
    range_padding = max(abs(min_ret - mean), abs(max_ret - mean))
    x_range = [mean - range_padding, mean + range_padding]
    fig = go.Figure()
    fig.add_trace(go.Histogram(
        x=df['Return'],
        nbinsx=200,  # More bins for finer bars
        name='Return (in ticks)',
        marker_color='green',
        opacity=0.7,
        xbins=dict(
            start=x_range[0],
            end=x_range[1],
            size=(x_range[1] - x_range[0]) / 200
        )
    ))
    # Add vertical lines and return annotations for SDs (in return units)
    for sd in [-3, -2, -1, 0, 1, 2, 3]:
        ret = mean + sd * std
        fig.add_shape(
            type='line',
            x0=ret, x1=ret,
            y0=0, y1=1,
            yref='paper',
            line=dict(
                color='red' if sd == 0 else 'gray',
                width=2 if sd == 0 else 1,
                dash='dash' if sd != 0 else 'solid'
            )
        )
        fig.add_annotation(
            x=ret,
            y=1,
            yref='paper',
            text=f'SD={sd}<br>Return={ret:.4f}',
            showarrow=False,
            yshift=10 if sd > 0 else -10,
            font=dict(color='red' if sd == 0 else 'gray')
        )
    fig.update_layout(
        title=f'Return Distribution (in ticks) - {title}',
        xaxis_title='Return (in ticks)',
        yaxis_title='Frequency',
        height=500,
        bargap=0.01,
        xaxis=dict(range=x_range, zeroline=True, zerolinewidth=2, zerolinecolor='black')
    )

    fig.show()

# Example usage:
# plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc6_ohlcv_1d.csv')
plot_standardized_return_histogram('Cleaned_Data/resampled_1d/FEIc6_ohlcv_1d.csv')

### Moving Averages and Bollinger Bands

In [92]:
def plot_ma_bollinger_bands(file_path):
    """
    Plot Close price with 10, 50, 100 period moving averages and their respective Bollinger Bands (±2 std).
    The color of each MA and its Bollinger Band is the same (with bands as transparent fill).
    Also plot rolling volatility (std) for each MA window on a secondary y-axis (right side).
    """
    import pandas as pd
    import plotly.graph_objs as go
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    
    ma_periods = [10, 50, 100]
    ma_colors = ['blue', 'orange', 'green']
    
    fig = go.Figure()
    # Plot Close price (darker color)
    fig.add_trace(go.Scatter(
        x=df['Date-Time'], y=df['Close'], name='Close',
        line=dict(color='black', width=2.5), opacity=1, yaxis='y1'
    ))
    
    for period, color in zip(ma_periods, ma_colors):
        ma = df['Close'].rolling(window=period).mean()
        std = df['Close'].rolling(window=period).std()
        # Extrapolate MA and std to initial dates by linear extrapolation (using first two valid values)
        first_valid = ma.first_valid_index()
        if first_valid is not None and first_valid > 0:
            # Linear extrapolation for MA
            next_valid = ma[first_valid+1:first_valid+2].index
            if len(next_valid) > 0:
                slope_ma = (ma[next_valid[0]] - ma[first_valid]) / (next_valid[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    ma[i] = ma[i+1] - slope_ma
            # Linear extrapolation for std
            next_valid_std = std[first_valid+1:first_valid+2].index
            if len(next_valid_std) > 0:
                slope_std = (std[next_valid_std[0]] - std[first_valid]) / (next_valid_std[0] - first_valid)
                for i in range(first_valid-1, -1, -1):
                    std[i] = std[i+1] - slope_std
        upper = ma + 2 * std
        lower = ma - 2 * std
        # MA line
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=ma, name=f'MA{period}',
            line=dict(color=color, width=2), yaxis='y1'
        ))
        # Bollinger Band (upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=upper, name=f'BB{period} Upper',
            line=dict(color=color, width=1, dash='dot'),
            showlegend=False, yaxis='y1'
        ))
        # Bollinger Band (lower, fill to upper)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=lower, name=f'BB{period} Lower',
            line=dict(color=color, width=1, dash='dot'),
            fill='tonexty', fillcolor='rgba(0,0,0,0.07)',
            opacity=0.2, showlegend=False, yaxis='y1'
        ))
        # Volatility (right y-axis)
        fig.add_trace(go.Scatter(
            x=df['Date-Time'], y=std, name=f'Volatility {period}',
            line=dict(color=color, width=2, dash='dash'),
            opacity=0.8, yaxis='y2'
        ))
    
    fig.update_layout(
        title='Close Price with Moving Averages, Bollinger Bands, and Volatility',
        xaxis_title='Date-Time',
        yaxis=dict(title='Price', side='left'),
        yaxis2=dict(title='Volatility', overlaying='y', side='right', showgrid=False),
        height=800,
        legend=dict(orientation='h', yanchor='bottom', y=1.02, xanchor='right', x=1)
    )
    fig.show()

# Example usage:
# plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc6_ohlcv_1d.csv')
plot_ma_bollinger_bands('Cleaned_Data/resampled_1d/FEIc6_ohlcv_1d.csv')

### Weekly and Monthly Heatmaps of Volume Traded and Returns

The following cell generates heatmaps showing the sum of volume traded and the sum of returns, grouped by ISO week (using the actual Monday-Sunday date range for each week) and by month, for quick visual analysis of trading activity and return patterns. Non-trading days are skipped in the aggregation.

In [93]:
import pandas as pd
import plotly.express as px
from datetime import timedelta

def plot_volume_return_heatmaps(file_path, tick_size=0.005):
    df = pd.read_csv(file_path)
    df['Date-Time'] = pd.to_datetime(df['Date-Time'])
    df['Date'] = df['Date-Time'].dt.date
    df['Year'] = df['Date-Time'].dt.isocalendar().year
    df['ISO_Week'] = df['Date-Time'].dt.isocalendar().week
    df['Month'] = df['Date-Time'].dt.month

    # Calculate returns as tick changes with configurable tick_size parameter
    df['Return'] = (df['Close'] - df['Close'].shift(1)) / tick_size
    df = df.dropna(subset=['Return'])

    # Group by ISO week (Monday-Sunday)
    df['WeekStart'] = df['Date-Time'].dt.to_period('W-MON').apply(lambda r: r.start_time.date())
    df['WeekEnd'] = df['WeekStart'] + timedelta(days=6)
    weekly = df.groupby(['Year', 'ISO_Week', 'WeekStart', 'WeekEnd']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    weekly['DateRange'] = weekly.apply(lambda x: f"{x['WeekStart']} to {x['WeekEnd']}", axis=1)

    # Monthly aggregation (using actual trading months)
    monthly = df.groupby(['Year', 'Month']).agg({'Volume': 'sum', 'Return': 'sum'}).reset_index()
    monthly['Year-Month'] = monthly['Year'].astype(str) + '-' + monthly['Month'].astype(str).str.zfill(2)

    # Weekly Volume Heatmap
    fig1 = px.imshow(
        [weekly['Volume'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Volume'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Volume Traded Heatmap (by ISO Week Date Range)'
    )
    fig1.show()

    # Weekly Return Heatmap
    fig2 = px.imshow(
        [weekly['Return'].values],
        labels=dict(x='Week (ISO Date Range)', y='', color='Return'),
        x=weekly['DateRange'],
        y=[''],
        aspect='auto',
        title='Weekly Returns Heatmap (by ISO Week Date Range)'
    )
    fig2.show()

    # Monthly Volume Heatmap
    fig3 = px.imshow(
        [monthly['Volume'].values],
        labels=dict(x='Year-Month', y='', color='Volume'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Volume Traded Heatmap'
    )
    fig3.show()

    # Monthly Return Heatmap
    fig4 = px.imshow(
        [monthly['Return'].values],
        labels=dict(x='Year-Month', y='', color='Return'),
        x=monthly['Year-Month'],
        y=[''],
        aspect='auto',
        title='Monthly Returns Heatmap'
    )
    fig4.show()

# Example usage:
# plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc6_ohlcv_1d.csv')
plot_volume_return_heatmaps('Cleaned_Data/resampled_1d/FEIc6_ohlcv_1d.csv')

c:\ProgramData\anaconda3\lib\site-packages\pandas\core\arrays\datetimes.py:1162: UserWarning:

Converting to PeriodArray/Index representation will drop timezone information.

